![Logo_Unifor](https://user-images.githubusercontent.com/61051085/81343928-3ce9d500-908c-11ea-9850-0210b4e94ba0.jpg)
# Projeto PLN01 - Ativ.02 - Análise Linguagem Ofensiva com Python 
    Disciplina: X503 - Mineração de Textos e Dados na Web | Professora Vládia
    
    Equipe 06 - Componentes:
    Antonio Marcos Aires Barbosa | Matrícula: 2016397
    Luis Carlos                  | Matrícula: 
    Marcus Vinícuis Miranda      | Matrícula: 

# RESOLUÇÃO:

# ATIVIDADE 01 - Pré-processamento dos textos (Prazo: 11/05/2020 - 30%)
1.1 NORMALIZAR              | Decisões de como será tratamento de dados de acordo com o problema abordado
        
        1.1.1 Captura/Carga | Ler colunas de interesse do arquivo texto, armazenar em dataset
        1.1.2 Limpeza       | Remoção apenas daqueles símbolos que causem falha no Python
        1.1.3 Stop-words    | Descartar palavras sem valor para análise

1.2 DIVIDIR (Tokenizer)     | Estudar melhor critério para obter a unidade subsentencial analisada (por palavra, sentença, etc)
        
        1.2.1 Por sentença, com pontuação (não obteve bons resultados de tokenização)
        1.2.2 Por sentença, sem pontuação (não obteve bons resultados de tokenização)
        1.2.3 Por palavras, com pontuação (não obteve bons resultados de tokenização)
        1.2.4 Por palavras, sem pontuação (não obteve bons resultados de tokenização)
        1.2.5 Por tweets,   sem pontuação (não obteve bons resultados de tokenização)
        1.2.6 Por tweets,   com pontuação (Escolhido para a tokenização)

1.3 ANOTAR (Tagger)          | Morfositaxe, classes de palavras individuais: pron, subst, ver, adv, conj, etc.
        
        1.3.1 Lematizar      | Deflexionar palavras para obter seu lema, eliminando flexões/lexemas (NÃO CONVÉM P/TWEETS)
        1.3.2 Stematizar     | Retirar desinências para reduzir ao radical da palavra (NÃO CONVÉM P/TWEETS)
        1.3.3 POS Tagging    | Part-Of-Speech Tagging, papel do termo: sujeito, predicado, verbo, etc.
        1.3.4 Chunking       | Classifar sintagmas, concordância gênero, número, com unidade semântica

In [2]:
#nltk.download('punkt')
#nltk.download('averaged_perceptron_tagger')
#nltk.download('wordnet')

# Importando os módulos necessários
import re
import nltk
import string
import pandas as pd 

from nltk.util import ngrams
from nltk.corpus import stopwords
from nltk.corpus import wordnet as wn
from nltk.stem import WordNetLemmatizer, PorterStemmer 
from nltk.tokenize import word_tokenize, TweetTokenizer, RegexpTokenizer
from nltk.tag import pos_tag

from sklearn.preprocessing import Binarizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer 

## Obtenção da lista de tweets a partir do arquivo de treinamento
# r_TSV = 'datasets/test.tsv'                     # Arquivo de teste
r_TSV = 'datasets/olid-training-v1.0.tsv'         # Caminho e nome do arquivo para leitura
w_CSV = 'dataset/analise-discurso.csv'            # Caminho e nome do arquivo para escrita
df = pd.read_csv(r_TSV, sep='\t', usecols=['tweet','subtask_a','subtask_b']) # lê o arquivo tsv como um csv separado por tabulações '\t' e armazena em um DataFrame

def penn_to_wn(tag):
    return get_wordnet_pos(tag)

#Funções usadas para limpar os dados
def remove_colchetes(column):                                            # Função para remover colchetes []
    for x in range(1,len(column)):
        return(re.sub('[\[\]]','',repr(column)))
    
def remove_pontuacao(column):                                            # Função para remover pontuação
    for x in range(1,len(column)):
        return(re.sub(r'[\\.?:;/“!&"0123456789]+','',repr(column)))

def remove_contracao(origem, destino, column):                           # Função para remover contrações e #
    for x in range(1,len(column)):
        return(re.sub(origem, destino, column))

origem, destino = '',''
linhas = []
lst_contr = [('’re',' are'), 
             ('’s',' is'), 
             ('n’t',' not'), 
             ('#', 'HASHTAG'), 
             ('&amp; ','')
            ]

for x in range(0,len(df['tweet'])):
    origem, destino = lst_contr[0]
    linha = remove_contracao(origem, destino, df['tweet'][x])
    for i in lst_contr:
        origem, destino = (i)
        linha = remove_contracao(origem, destino, linha)
    linhas.append(linha)

# Cria o novo DataFrame com tweets sem as stopwords, sem pontuações e sem contrações
dados = pd.DataFrame(linhas)
dados.columns = ['tweets']

# cria uma lista de stopwords oriunda do NLTK
nltk.download('stopwords')
stop_words = nltk.corpus.stopwords.words('english')

# Descomentar as linhas abaixo para remover somente stopwords e criar uma novo DataFrame com o resultado
use = dados['tweets']
re = '\w+|\$[\d\.]+|\S+' # separa por palavras e valores em moeda caracterizados por símbolos de $

lst_regextokenized = []
lst_taggedtoken = []
lst_lematized = []
lst_stemmed = []

wl = WordNetLemmatizer()
ps = PorterStemmer()

for x in range(0,len(use)):
    tokenizer = RegexpTokenizer(re)
    tokens = tokenizer.tokenize(use[x])                     # Gera tokens com tokenizer de regular expressions do NLTK 
    lst_regextokenized.append(tokens)
    
    stemmed=[]                                                             
    stemmed = [ps.stem(word) for word in tokens]            # Remove desinências, deixa apenas o radical da palavra
    lst_stemmed.append(stemmed)

    taggedtoken = nltk.pos_tag(tokens)                      # Classificação morfosintáxica
    lst_taggedtoken.append(taggedtoken)
    
    lematized=[]                                                             
    ttokenized = [w for w in tokens]
    lematized = [wl.lemmatize(word) for word in ttokenized] # Remove inflexões, deixa apenas o lema da palavra
    lst_lematized.append(lematized)
                                                            
df_regextokenized = pd.DataFrame(lst_regextokenized)
df_stemmed = pd.DataFrame(lst_stemmed)
df_taggedtokens = pd.DataFrame(lst_taggedtoken)
df_lematized = pd.DataFrame(lst_lematized)

print('Resultado da divisão em tokens:',df_taggedtokens.shape)

# Definindo o corpus
corpus = lst_lematized

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\marco\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Resultado da divisão em tokens: (13240, 109)


###### Cada POS Tagger possui seu conjunto de tags proprio.

    CC coordinating conjunction
    CD cardinal digit
    DT determiner
    EX existential there (like: “there is” … think of it like “there exists”)
    FW foreign word
    IN preposition/subordinating conjunction
    JJ adjective ‘big’
    JJR adjective, comparative ‘bigger’
    JJS adjective, superlative ‘biggest’
    LS list marker 1)
    MD modal could, will
    NN noun, singular ‘desk’
    NNS noun plural ‘desks’
    NNP proper noun, singular ‘Harrison’
    NNPS proper noun, plural ‘Americans’
    PDT predeterminer ‘all the kids’
    POS possessive ending parent‘s
    PRP personal pronoun I, he, she
    PRP' possessive pronoun my, his, hers
    RB adverb very, silently,
    RBR adverb, comparative better
    RBS adverb, superlative best
    RP particle give up
    TO to go ‘to‘ the store.
    UH interjection errrrrrrrm
    VB verb, base form take
    VBD verb, past tense took
    VBG verb, gerund/present participle taking
    VBN verb, past participle taken
    VBP verb, sing. present, non-3d take
    VBZ verb, 3rd person sing. present takes
    WDT wh-determiner which
    WP wh-pronoun who, what
    WP' possessive wh-pronoun whose
    WRB wh-abverb where, when

In [3]:
df.head(5)

tweet subtask_a subtask_b
0  @USER She should ask a few native Americans wh...       OFF       UNT
1  @USER @USER Go home you’re drunk!!! @USER #MAG...       OFF       TIN
2  Amazon is investigating Chinese employees who ...       NOT       NaN
3  @USER Someone should'veTaken" this piece of sh...       OFF       UNT
4  @USER @USER Obama wanted liberals &amp; illega...       NOT       NaN

In [4]:
dados.head(5)

tweets
0  @USER She should ask a few native Americans wh...
1  @USER @USER Go home you are drunk!!! @USER HAS...
2  Amazon is investigating Chinese employees who ...
3  @USER Someone should'veTaken" this piece of sh...
4  @USER @USER Obama wanted liberals illegals to ...

In [5]:
df_regextokenized.head(5)

0        1              2          3          4         5       6    \
0   @USER      She         should        ask          a       few  native   
1   @USER    @USER             Go       home        you       are   drunk   
2  Amazon       is  investigating    Chinese  employees       who     are   
3   @USER  Someone         should  'veTaken"       this     piece      of   
4   @USER    @USER          Obama     wanted   liberals  illegals      to   

         7         8            9    ...   99    100   101   102   103   104  \
0  Americans      what        their  ...  None  None  None  None  None  None   
1        !!!     @USER  HASHTAGMAGA  ...  None  None  None  None  None  None   
2    selling  internal         data  ...  None  None  None  None  None  None   
3       shit        to            a  ...  None  None  None  None  None  None   
4       move      into          red  ...  None  None  None  None  None  None   

    105   106   107   108  
0  None  None  None  None  
1  None  None  None  None  
2  None  None  None  None  
3  None  None  None  None  
4  None  None  None  None  

[5 rows x 109 columns]

In [6]:
df_stemmed.head(5)

0       1         2          3        4      5      6         7    \
0   @user     she    should        ask        a    few  nativ  american   
1   @user   @user        Go       home      you    are  drunk       !!!   
2  amazon      is  investig     chines  employe    who    are      sell   
3   @user  someon    should  'vetaken"      thi   piec     of      shit   
4   @user   @user     obama       want    liber  illeg     to      move   

      8            9    ...   99    100   101   102   103   104   105   106  \
0    what        their  ...  None  None  None  None  None  None  None  None   
1   @user  hashtagmaga  ...  None  None  None  None  None  None  None  None   
2  intern         data  ...  None  None  None  None  None  None  None  None   
3      to            a  ...  None  None  None  None  None  None  None  None   
4    into          red  ...  None  None  None  None  None  None  None  None   

    107   108  
0  None  None  
1  None  None  
2  None  None  
3  None  None  
4  None  None  

[5 rows x 109 columns]

In [7]:
df_taggedtokens.head(5)

0               1                     2                3    \
0    (@USER, IN)      (She, PRP)          (should, MD)        (ask, VB)   
1    (@USER, VB)    (@USER, NNP)             (Go, NNP)       (home, NN)   
2  (Amazon, NNP)       (is, VBZ)  (investigating, VBG)    (Chinese, JJ)   
3    (@USER, IN)  (Someone, NNP)          (should, MD)  ('veTaken", VB)   
4   (@USER, NNS)    (@USER, VBP)          (Obama, NNP)    (wanted, VBD)   

                4                5             6                  7    \
0           (a, DT)        (few, JJ)  (native, JJ)  (Americans, NNPS)   
1        (you, PRP)       (are, VBP)   (drunk, JJ)         (!!!, NNP)   
2  (employees, NNS)        (who, WP)    (are, VBP)     (selling, VBG)   
3        (this, DT)      (piece, NN)      (of, IN)         (shit, NN)   
4   (liberals, NNS)  (illegals, NNS)      (to, TO)         (move, VB)   

              8                   9    ...   99    100   101   102   103  \
0      (what, WP)       (their, PRP$)  ...  None  None  None  None  None   
1    (@USER, NNP)  (HASHTAGMAGA, NNP)  ...  None  None  None  None  None   
2  (internal, JJ)         (data, NNS)  ...  None  None  None  None  None   
3        (to, TO)             (a, DT)  ...  None  None  None  None  None   
4      (into, IN)           (red, JJ)  ...  None  None  None  None  None   

    104   105   106   107   108  
0  None  None  None  None  None  
1  None  None  None  None  None  
2  None  None  None  None  None  
3  None  None  None  None  None  
4  None  None  None  None  None  

[5 rows x 109 columns]

In [8]:
df_lematized.head(5)

0        1              2          3         4         5       6    \
0   @USER      She         should        ask         a       few  native   
1   @USER    @USER             Go       home       you       are   drunk   
2  Amazon       is  investigating    Chinese  employee       who     are   
3   @USER  Someone         should  'veTaken"      this     piece      of   
4   @USER    @USER          Obama     wanted   liberal  illegals      to   

         7         8            9    ...   99    100   101   102   103   104  \
0  Americans      what        their  ...  None  None  None  None  None  None   
1        !!!     @USER  HASHTAGMAGA  ...  None  None  None  None  None  None   
2    selling  internal         data  ...  None  None  None  None  None  None   
3       shit        to            a  ...  None  None  None  None  None  None   
4       move      into          red  ...  None  None  None  None  None  None   

    105   106   107   108  
0  None  None  None  None  
1  None  None  None  None  
2  None  None  None  None  
3  None  None  None  None  
4  None  None  None  None  

[5 rows x 109 columns]

In [9]:
## Necessário download somente na primeira instalação se não houverem no Anaconda ainda
# nltk.download('maxent_ne_chunker')
# nltk.download('words')
from nltk.tokenize import RegexpTokenizer
from nltk.tag import pos_tag
from nltk.tree import Tree 
from nltk.chunk.regexp import ChunkString, ChunkRule, ChinkRule 
from nltk.chunk import RegexpChunkParser 
from nltk.chunk import conlltags2tree, tree2conlltags
from pprint import pprint

use = dados['tweets']
re = '\w+|\$[\d\.]+|\S+' # separa por palavras e valores em moeda caracterizados por símbolos de $

pattern = 'NP: {<DT>?<JJ>*<NN>}'
pattern1 = 'NP: {<DT>?<JJ>*<NN.*>*}'
pattern2 = 'NP: {<DT><NN.*><.*>*<NN.*>}'

for x in range(0,len(use)):
    tokenizer = RegexpTokenizer(re)
    tokens = tokenizer.tokenize(use[x])                    # Gera tokens com tokenizer de regular expressions do NLTK
    taggedtoken = nltk.pos_tag(tokens)
    
    sent = taggedtoken
    cp = nltk.RegexpParser(pattern1)
    cs = cp.parse(sent)
    iob_tagged = tree2conlltags(cs)
#     tree = Tree('S', [('the', 'DT'), ('book', 'NN'),('has', 'VBZ'), ('many', 'JJ'), ('chapters', 'NNS')]) 
    tree = Tree('S', iob_tagged)
    chunk_string = ChunkString(tree) 
#     chunk_rule = ChunkRule(pattern1, 'chunk determinantes, adjetivos e nomes') 
#     chunk_rule.apply(chunk_string)
    print ("\nTweet",x+1,':', sent, chunk_string) 


Tweet 1 : [('@USER', 'IN'), ('She', 'PRP'), ('should', 'MD'), ('ask', 'VB'), ('a', 'DT'), ('few', 'JJ'), ('native', 'JJ'), ('Americans', 'NNPS'), ('what', 'WP'), ('their', 'PRP$'), ('take', 'NN'), ('on', 'IN'), ('this', 'DT'), ('is', 'VBZ'), ('.', '.')]  <IN>  <PRP>  <MD>  <VB>  <DT>  <JJ>  <JJ>  <NNPS>  <WP>  <PRP$>  <NN>  <IN>  <DT>  <VBZ>  <.> 

Tweet 2 : [('@USER', 'VB'), ('@USER', 'NNP'), ('Go', 'NNP'), ('home', 'NN'), ('you', 'PRP'), ('are', 'VBP'), ('drunk', 'JJ'), ('!!!', 'NNP'), ('@USER', 'NNP'), ('HASHTAGMAGA', 'NNP'), ('HASHTAGTrump2020', 'NNP'), ('👊🇺🇸👊', 'NNP'), ('URL', 'NNP')]  <VB>  <NNP>  <NNP>  <NN>  <PRP>  <VBP>  <JJ>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP> 

Tweet 3 : [('Amazon', 'NNP'), ('is', 'VBZ'), ('investigating', 'VBG'), ('Chinese', 'JJ'), ('employees', 'NNS'), ('who', 'WP'), ('are', 'VBP'), ('selling', 'VBG'), ('internal', 'JJ'), ('data', 'NNS'), ('to', 'TO'), ('third', 'VB'), ('-party', 'JJ'), ('sellers', 'NNS'), ('looking', 'VBG'), ('for', 'IN'), ('an', '

Tweet 79 : [('@USER', 'NN'), ('She', 'PRP'), ('is', 'VBZ'), ('a', 'DT'), ('beautiful', 'JJ'), ('person', 'NN'), ('to', 'TO'), ('teach', 'VB'), ('values', 'NNS'), ('to', 'TO'), ('her', 'PRP$'), ('kids', 'NNS'), ('.', '.'), ('Teaching', 'VBG'), ('them', 'PRP'), ('they', 'PRP'), ('are', 'VBP'), ('royalty', 'NN'), ('but', 'CC'), ('keep', 'VB'), ('to', 'TO'), ('keep', 'VB'), ('it', 'PRP'), ('from', 'IN'), ('going', 'VBG'), ('to', 'TO'), ('their', 'PRP$'), ('heads', 'NNS'), ('.', '.'), ('Stay', 'NNP'), ('real', 'JJ'), ('❤️', 'NN')]  <NN>  <PRP>  <VBZ>  <DT>  <JJ>  <NN>  <TO>  <VB>  <NNS>  <TO>  <PRP$>  <NNS>  <.>  <VBG>  <PRP>  <PRP>  <VBP>  <NN>  <CC>  <VB>  <TO>  <VB>  <PRP>  <IN>  <VBG>  <TO>  <PRP$>  <NNS>  <.>  <NNP>  <JJ>  <NN> 

Tweet 80 : [('@USER', 'RB'), ('Bring', 'VBG'), ('out', 'RP'), ('his', 'PRP$'), ('Antifa', 'NNP'), ('criminal', 'JJ'), ('son', 'NN'), ('to', 'TO'), ('campaign', 'NN'), ('for', 'IN'), ('him', 'PRP')]  <RB>  <VBG>  <RP>  <PRP$>  <NNP>  <JJ>  <NN>  <TO>  <NN>  <IN

Tweet 167 : [('@USER', 'NN'), ('Who', 'WP'), ('are', 'VBP'), ('“they”', 'JJ'), ('Gun', 'NNP'), ('control', 'NN'), ('has', 'VBZ'), ('been', 'VBN'), ('tried', 'VBN'), ('and', 'CC'), ('is', 'VBZ'), ('a', 'DT'), ('proven', 'JJ'), ('failure', 'NN'), ('.', '.'), ('This', 'DT'), ('is', 'VBZ'), ('why', 'WRB'), ('people', 'NNS'), ('do', 'VBP'), ('not', 'RB'), ('vote', 'VB'), ('democrat', 'NN'), ('.', '.'), ('They', 'PRP'), ('refuse', 'VBP'), ('to', 'TO'), ('admit', 'VB'), ('reality', 'NN'), ('.', '.'), ('Gun', 'NNP'), ('control', 'NN'), ('does', 'VBZ'), ('not', 'RB'), ('work', 'VB'), ('.', '.')]  <NN>  <WP>  <VBP>  <JJ>  <NNP>  <NN>  <VBZ>  <VBN>  <VBN>  <CC>  <VBZ>  <DT>  <JJ>  <NN>  <.>  <DT>  <VBZ>  <WRB>  <NNS>  <VBP>  <RB>  <VB>  <NN>  <.>  <PRP>  <VBP>  <TO>  <VB>  <NN>  <.>  <NNP>  <NN>  <VBZ>  <RB>  <VB>  <.> 

Tweet 168 : [('@USER', 'NNS'), ('So', 'RB'), ('the', 'DT'), ('overwhelming', 'JJ'), ('liberals', 'NNS'), ('in', 'IN'), ('the', 'DT'), ('populated', 'JJ'), ('states', 'NNS'), ('ca

Tweet 252 : [('@USER', 'NN'), ('Yet', 'CC'), ('she', 'PRP'), ('is', 'VBZ'), ('fat', 'JJ'), ('herself', 'PRP'), ('.', '.')]  <NN>  <CC>  <PRP>  <VBZ>  <JJ>  <PRP>  <.> 

Tweet 253 : [('@USER', 'RB'), ('@USER', 'NN'), ('There', 'EX'), ('was', 'VBD'), ('plenty', 'NN'), ('of', 'IN'), ('evidence', 'NN'), ('that', 'IN'), ('he', 'PRP'), ('was', 'VBD'), ('guilty', 'JJ'), ('of', 'IN'), ('what', 'WP'), ('Hill', 'NNP'), ('accused', 'VBD'), ('him', 'PRP'), ('of', 'IN'), ('but', 'CC'), ('since', 'IN'), ('conf', 'JJ'), ('hearings', 'NNS'), ('aren', 'IN'), ("'t", 'CD'), ('about', 'IN'), ('guilty', 'JJ'), ('/innocence', 'NN'), ('got', 'VBD'), ('on', 'IN'), ('the', 'DT'), ('bench', 'NN'), ('.', '.'), ('Times', 'NNS'), ('are', 'VBP'), ('diff', 'JJ'), ('now', 'RB'), ('.', '.'), ('Why', 'WRB'), ('as', 'IN'), ('a', 'DT'), ('journalist', 'NN'), ('you', 'PRP'), ('don', 'VBP'), ("'t", "''"), ('call', 'VB'), ('out', 'RP'), ('white', 'JJ'), ('supremacy', 'NN'), ('/alt-right', 'JJ'), ('but', 'CC'), ('Antifa', 'N

Tweet 339 : [('@USER', 'JJ'), ('HELLO', 'NNP'), ('SOMEBODY', 'NNP'), ('NEED', 'NNP'), ('HYUKJAE', 'NNP'), ('NOW', 'NNP'), ('SHE', 'NNP'), ('IS', 'VBZ'), ('IN', 'NNP'), ('DANGER', 'NNP'), ('BY', 'NNP'), ('WATCHING', 'NNP'), ('YOUR', 'NNP'), ('FANCAMS', 'NNP')]  <JJ>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <VBZ>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP> 

Tweet 340 : [('@USER', 'NN'), ('He', 'PRP'), ('never', 'RB'), ('did', 'VBD'), ('show', 'VB'), ('much', 'JJ'), ('intelligence', 'NN'), ('.', '.')]  <NN>  <PRP>  <RB>  <VBD>  <VB>  <JJ>  <NN>  <.> 

Tweet 341 : [('@USER', 'JJ'), ('Yes', 'NNP'), ('I', 'PRP'), ('saw', 'VBD'), ('this', 'DT'), ('and', 'CC'), ('I', 'PRP'), ('will', 'MD'), ('say', 'VB'), ('tapper', 'JJ'), ('kept', 'NN'), ('basket', 'NN'), ('her', 'PRP$'), ('and', 'CC'), ('she', 'PRP'), ('kept', 'VBD'), ('coming', 'VBG'), ('back', 'RB'), ('with', 'IN'), ('stupid', 'JJ'), ('answers', 'NNS'), ('And', 'CC'), ('he', 'PRP'), ('finally', 'RB'), ('gave', 'VBD'), ('up', 'RP'), ('I', 

...

Tweet 12853 : [('@USER', 'NN'), ('Bob', 'NNP'), ('is', 'VBZ'), ('an', 'DT'), ('old', 'JJ'), ('man', 'NN'), ('living', 'NN'), ('in', 'IN'), ('the', 'DT'), ('past', 'NN'), ('.', '.'), ('He', 'PRP'), ('has', 'VBZ'), ('no', 'DT'), ('idea', 'NN'), ('what', 'WP'), ('the', 'DT'), ('working', 'VBG'), ('class', 'NN'), ('has', 'VBZ'), ('been', 'VBN'), ('through', 'IN'), ('.', '.'), ('Promises', 'NNS'), ('from', 'IN'), ('both', 'DT'), ('the', 'DT'), ('Dems', 'NNP'), ('Rep', 'NNP'), ('career', 'NN'), ('politicians', 'NNS'), ('with', 'IN'), ('their', 'PRP$'), ('expensive', 'JJ'), ('law', 'NN'), ('degrees', 'NNS'), ('and', 'CC'), ('never', 'RB'), ('worked', 'VBD'), ('a', 'DT'), ('day', 'NN'), ('in', 'IN'), ('their', 'PRP$'), ('lives', 'NNS'), ('.', '.'), ('It', 'PRP'), ('took', 'VBD'), ('@USER', 'NN'), ('to', 'TO'), ('finally', 'RB'), ('listen', 'VB'), ('and', 'CC'), ('take', 'VB'), ('action', 'NN'), ('.', '.')]  <NN>  <NNP>  <VBZ>  <DT>  <JJ>  <NN>  <NN>  <IN>  <DT>  <NN>  <.>  <PRP>  <VBZ>  <DT>  

Tweet 12938 : [('HASHTAGWashingtonPost', 'NNP'), ('broke', 'VBD'), ('the', 'DT'), ('story', 'NN'), ('therapist', 'NN'), ('notes', 'NNS'), ('Miss', 'NNP'), ('Ford', 'NNP'), ('stated', 'VBD'), ('four', 'CD'), ('men', 'NNS'), ('assaulted', 'VBD'), ('her', 'PRP'), ('😠', 'NN'), ('now', 'RB'), ('it', 'PRP'), ("'s", 'VBZ'), ('two', 'CD'), ('😮', 'NN'), ('HASHTAGVoteDemsOut', 'NNP'), ('to', 'TO'), ('end', 'VB'), ('HASHTAGDirtyTricks', 'NNP'), ('stop', 'VB'), ('what', 'WP'), ("'s", 'VBZ'), ('wrong', 'JJ'), ('with', 'IN'), ('HASHTAGDC', 'NNP'), ('HASHTAGKavanaugh', 'NNP'), ('HASHTAGmaga', 'NNP'), ('HASHTAGFoxNews', 'NNP'), ('HASHTAGLiar', 'NNP'), ('HASHTAGCNN', 'NNP'), ('HASHTAGmsnbc', 'NNP'), ('HASHTAGSenFlake', 'NNP'), ('HASHTAGWrong', 'NNP'), ('to', 'TO'), ('use', 'VB'), ('HASHTAGMeToo', 'NNP'), ('for', 'IN'), ('politics', 'NNS'), ('HASHTAGChristineBlaseyFord', 'NNP'), ('URL', 'NNP')]  <NNP>  <VBD>  <DT>  <NN>  <NN>  <NNS>  <NNP>  <NNP>  <VBD>  <CD>  <NNS>  <VBD>  <PRP>  <NN>  <RB>  <PRP>  <VB

Tweet 13024 : [('@USER', 'JJ'), ('Let', 'NNP'), ("'s", 'POS'), ('not', 'RB'), ('kid', 'VB'), ('ourselves', 'PRP'), ('...you', 'PRP'), ('are', 'VBP'), ('a', 'DT'), ('prostitute', 'NN'), ('...for', 'VBZ'), ('the', 'DT'), ('@USER', 'NN')]  <JJ>  <NNP>  <POS>  <RB>  <VB>  <PRP>  <PRP>  <VBP>  <DT>  <NN>  <VBZ>  <DT>  <NN> 

Tweet 13025 : [('@USER', 'NN'), ('RIP', 'NNP'), ('The', 'DT'), ('promotion', 'NN'), ('you', 'PRP'), ('are', 'VBP'), ('trying', 'VBG'), ('to', 'TO'), ('access', 'NN'), ('has', 'VBZ'), ('ended', 'VBN'), ('"', 'NN'), ('shows', 'VBZ'), ('up', 'RP'), ('"', 'NNS')]  <NN>  <NNP>  <DT>  <NN>  <PRP>  <VBP>  <VBG>  <TO>  <NN>  <VBZ>  <VBN>  <NN>  <VBZ>  <RP>  <NNS> 

Tweet 13026 : [('@USER', 'NNS'), ('@USER', 'VBP'), ('@USER', 'NNP'), ('@USER', 'NNP'), ('Police', 'NNP'), ('reform', 'NN'), ('yes', 'RB'), ('.', '.'), ('We', 'PRP'), ('should', 'MD'), ('try', 'VB'), ('that', 'DT'), ('.', '.'), ('Gun', 'VB'), ('control', 'NN'), ('?', '.'), ('We', 'PRP'), ('’ve', 'VBP'), ('tried', 'VBD

Tweet 13109 : [('@USER', 'NN'), ('@USER', 'NN'), ('She', 'PRP'), ('is', 'VBZ'), ('asking', 'VBG'), ('questions', 'NNS'), ('there', 'EX'), ('are', 'VBP'), ('no', 'DT'), ('answers', 'NNS'), ('for', 'IN'), ('.', '.')]  <NN>  <NN>  <PRP>  <VBZ>  <VBG>  <NNS>  <EX>  <VBP>  <DT>  <NNS>  <IN>  <.> 

Tweet 13110 : [('@USER', 'NN'), ('@USER', 'NN'), ('She', 'PRP'), ('held', 'VBD'), ('on', 'IN'), ('to', 'TO'), ('something', 'NN'), ('“almost”', 'RP'), ('happening', 'VBG'), ('(according', 'VBG'), ('to', 'TO'), ('her', 'PRP$'), (')', ')'), ('for', 'IN'), ('35', 'CD'), ('yrs', 'NNS'), ('and', 'CC'), ('then', 'RB'), ('decides', 'VBZ'), ('to', 'TO'), ('try', 'VB'), ('and', 'CC'), ('ruin', 'VB'), ('his', 'PRP$'), ('life', 'NN'), ('?', '.'), ('She', 'PRP'), ('is', 'VBZ'), ('the', 'DT'), ('despicable', 'JJ'), ('.', '.'), ('Regardless', 'NNP'), ('of', 'IN'), ('what', 'WP'), ('did', 'VBD'), ('or', 'CC'), ('did', 'VBD'), ('not', 'RB'), ('happen', 'VB'), ('.', '.')]  <NN>  <NN>  <PRP>  <VBD>  <IN>  <TO>  <NN

Tweet 13194 : [('@USER', 'RB'), ('More', 'JJR'), ('press', 'NN'), ('should', 'MD'), ('talk', 'VB'), ('about', 'IN'), ('this', 'DT'), ('remarkable', 'JJ'), ('20yr', 'CD'), ('old', 'JJ'), ('she', 'PRP'), ('is', 'VBZ'), ('the', 'DT'), ('future', 'NN')]  <RB>  <JJR>  <NN>  <MD>  <VB>  <IN>  <DT>  <JJ>  <CD>  <JJ>  <PRP>  <VBZ>  <DT>  <NN> 

Tweet 13195 : [('@USER', 'NNS'), ('@USER', 'NNP'), ('HASHTAGMohammadHassanKhalid', 'NNP'), ('is', 'VBZ'), ('a', 'DT'), ('HASHTAGtraitor', 'NN'), ('to', 'TO'), ('the', 'DT'), ('HASHTAGUSA', 'NNP'), ('to', 'TO'), ('his', 'PRP$'), ('fellow', 'JJ'), ('HASHTAGIslamists', 'NNPS'), ('He', 'PRP'), ('is', 'VBZ'), ('unlikely', 'JJ'), ('to', 'TO'), ('enjoy', 'VB'), ('a', 'DT'), ('long', 'JJ'), ('happy', 'JJ'), ('healthy', 'JJ'), ('life', 'NN'), ('based', 'VBN'), ('on', 'IN'), ('very', 'RB'), ('poor', 'JJ'), ('decision', 'NN'), ('making', 'VBG'), ('skills', 'NNS'), ('values', 'NNS')]  <NNS>  <NNP>  <NNP>  <VBZ>  <DT>  <NN>  <TO>  <DT>  <NNP>  <TO>  <PRP$>  <JJ>  <N

In [10]:
# Exemplo de como criar uma ChinkRule 
chink_rule = ChinkRule('<VB.*>', 'chink verbs') 
chink_rule.apply(chunk_string) 
print ("\nApplied ChinkRule : ", chink_rule, chunk_string, "\n") 


Applied ChinkRule :  <ChinkRule: '<VB.*>'>  <NNP>  <NN>  <.>  <NNP>  <NNPS>  <CC>  <NNP>  <NNP>  <VBZ>  <DT>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  <NNP>  




# ATIVIDADE 02 - Processamento dos textos (Prazo: 03/07/2020 - 30%)
1.4 ANÁLISE SEMÂNTICA      
        
        1.4.1 NER            | Análise de dependência no contexto semântico
        1.4.2 Extrair BOW    | Extrair unigramas e bigramas
        1.4.3 BasesExternas  | a)WordNet, b)Empath... sinônimos, hiperônimos, advérbios podem ser desconsiderados 
        1.4.4 Word-Embeedings| Vetorização, recuperar word embeedings conjunto de dados já pré-treinados (SentiWordNet??)

# 1.4.1 NER palavra (com Spacy)

localizar e classificar as entidades mencionadas em um texto escrito em linguagem natural, e classificá-las em categorias pré-definidas tais como PESSOA, ORGANIZAÇÃO, LOCAL, TEMPO, VALORES, etc.

In [11]:
## Necessário só na primeira instalação quando ainda não instalado no Anaconda
# !pip install spacy
# !python -m spacy download en_core_web_sm

In [12]:
## Reconhecimento de Entidades Noeadas NER
import spacy 

from spacy import displacy
from collections import Counter
import en_core_web_sm
nlp = en_core_web_sm.load()

use = dados['tweets']
re = '\w+|\$[\d\.]+|\S+'

for x in range(0,len(use)):
    tokenizer = RegexpTokenizer(re)
    tokens = tokenizer.tokenize(use[x])                    # Gera tokens com tokenizer de regular expressions do NLTK
    
    doc = nlp(str(tokens))
#     print('Tokens do Tweet',x+1,':', str(tokens))
#     print("\nEntidades e Tipos:")
#     pprint([(X.text, X.label_) for X in doc.ents])
#     print("\n")

## Impressão de entidades no formato IOB
    # "B" significa que o token está no começo de uma entidade, 
    # "I" significa que o token está dentro de uma entidade, 
    # "O" significa que o token está fora de uma entidade, e 
    # "" significa que nenhuma entidade está selecionada.

# 1.4.2. BOW - Extração de N-Gramas 

In [14]:
# # Instalações necessárias só na primeira vez para instalar no Anaconda
# nltk.download('punkt')
# nltk.download('averaged_perceptron_tagger')
# nltk.download('wordnet')

# Importando os módulos necessários
from nltk.corpus import stopwords
from nltk.corpus import wordnet as wn
from nltk.tokenize import RegexpTokenizer
from nltk.util import ngrams

def word_grams(words, n):
     s = []
     for ngram in ngrams(words, n):
         s.append(' '.join(str(i) for i in ngram))
     return s

use = dados['tweets']
re = '\w+|\$[\d\.]+|\S+'
lst_unigrams=[]
lst_bigrams=[]

for x in range(0,len(use)):
    tokenizer = RegexpTokenizer(re)
    tokens = tokenizer.tokenize(use[x])
    lst_regextokenized.append(tokens) 
    unigrams = word_grams(tokens,1)
    lst_unigrams.append(unigrams)
    bigrams = word_grams(tokens,2)
    lst_bigrams.append(bigrams)

# lst_unigrams = word_grams(['um','dois','três','quatro'],1)
df_unigrams = pd.DataFrame(lst_unigrams)

# lst_bigrams = word_grams(['um','dois','três','quatro'],2)
df_bigrams = pd.DataFrame(lst_bigrams)

In [15]:
df_unigrams.head(5)

0        1              2          3          4         5       6    \
0   @USER      She         should        ask          a       few  native   
1   @USER    @USER             Go       home        you       are   drunk   
2  Amazon       is  investigating    Chinese  employees       who     are   
3   @USER  Someone         should  'veTaken"       this     piece      of   
4   @USER    @USER          Obama     wanted   liberals  illegals      to   

         7         8            9    ...   99    100   101   102   103   104  \
0  Americans      what        their  ...  None  None  None  None  None  None   
1        !!!     @USER  HASHTAGMAGA  ...  None  None  None  None  None  None   
2    selling  internal         data  ...  None  None  None  None  None  None   
3       shit        to            a  ...  None  None  None  None  None  None   
4       move      into          red  ...  None  None  None  None  None  None   

    105   106   107   108  
0  None  None  None  None  
1  None  None  None  None  
2  None  None  None  None  
3  None  None  None  None  
4  None  None  None  None  

[5 rows x 109 columns]

In [16]:
df_bigrams.head(5)

0                 1                      2                  3    \
0      @USER She        She should             should ask              ask a   
1    @USER @USER          @USER Go                Go home           home you   
2      Amazon is  is investigating  investigating Chinese  Chinese employees   
3  @USER Someone    Someone should       should 'veTaken"     'veTaken" this   
4    @USER @USER       @USER Obama           Obama wanted    wanted liberals   

                 4            5                 6                 7    \
0              a few   few native  native Americans    Americans what   
1            you are    are drunk         drunk !!!         !!! @USER   
2      employees who      who are       are selling  selling internal   
3         this piece     piece of           of shit           shit to   
4  liberals illegals  illegals to           to move         move into   

                 8                             9    ...   98    99    100  \
0         what their                    their take  ...  None  None  None   
1  @USER HASHTAGMAGA  HASHTAGMAGA HASHTAGTrump2020  ...  None  None  None   
2      internal data                       data to  ...  None  None  None   
3               to a                     a volcano  ...  None  None  None   
4           into red                    red states  ...  None  None  None   

    101   102   103   104   105   106   107  
0  None  None  None  None  None  None  None  
1  None  None  None  None  None  None  None  
2  None  None  None  None  None  None  None  
3  None  None  None  None  None  None  None  
4  None  None  None  None  None  None  None  

[5 rows x 108 columns]

In [17]:
#nltk.download('punkt')
#nltk.download('averaged_perceptron_tagger')
#nltk.download('wordnet')

# 1.4.4 Word-Embeedings - Vetorizacao por TF-IDF  com n-gram

In [35]:
# USANDO SCIKIT-LEARN - Vetorizacao usando Bigrama / Trigrama por TFIDF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer 
from sklearn.preprocessing import Binarizer

print('\n------- VETORIZACAO POR TFIDF (BIGRAMA) - Scikit Learn -------\n')
# Recuperando bigramas  
for bigram in lst_bigrams:
    vectorizer = CountVectorizer(ngram_range = (2,2)) 
    X1 = vectorizer.fit_transform(bigram)  
    features = (vectorizer.get_feature_names()) 
#     print("\n\nFeatures : \n", features) 
#     print("\n\nX1 : \n", X1.toarray()) 
  
    # Aplicando TFIDF 
    vectorizer = TfidfVectorizer(ngram_range = (2,2)) 
    X2 = vectorizer.fit_transform(bigram) 
    scores = (X2.toarray()) 
#     print("\n\nScores : \n", scores) 

    # TOP RANKING features 
    sums = X2.sum(axis = 0) 
    data1 = [] 
    for col, term in enumerate(features): 
        data1.append( (term, sums[0, col] )) 
    ranking = pd.DataFrame(data1, columns = ['Bigrama', 'rank']) 
    words = (ranking.sort_values('rank', ascending = False)) 
    print ("\n\nWords : \n", words.head(10)) 


------- VETORIZACAO POR TFIDF (BIGRAMA) - Scikit Learn -------



Words : 
             Bigrama  rank
0    americans what   1.0
1        few native   1.0
2  native americans   1.0
3           on this   1.0
4        she should   1.0
5        should ask   1.0
6           take on   1.0
7        their take   1.0
8           this is   1.0
9          user she   1.0


Words : 
                         Bigrama  rank
0                     are drunk   1.0
1                       go home   1.0
2  hashtagmaga hashtagtrump2020   1.0
3                      home you   1.0
4                       user go   1.0
5              user hashtagmaga   1.0
6                     user user   1.0
7                       you are   1.0


Words : 
               Bigrama  rank
0           amazon is   1.0
1             an edge   1.0
24  url hashtagamazon   1.0
23           to third   1.0
22        third party   1.0
21    the competitive   1.0
20   selling internal   1.0
19    sellers looking   1.0
18      party selle

14        no horse   1.0


Words : 
            Bigrama  rank
2           and so   2.0
27       user user   2.0
20           so on   2.0
0   americas worst   1.0
16       not gunna   1.0
29          way to   1.0
28       user what   1.0
26          usa is   1.0
25         to take   1.0
24         the usa   1.0


Words : 
        Bigrama  rank
0  her wedding   1.0
1      is very   1.0
2       me too   1.0
3       she is   1.0
4     the best   1.0
5      user me   1.0
6  very pretty   1.0
7      was the   1.0
8  wedding was   1.0


Words : 
         Bigrama  rank
0     agenda of   1.0
9   left agenda   1.0
15    user user   1.0
14      user no   1.0
13    of antifa   1.0
12     not look   1.0
11  no conflict   1.0
10      look at   1.0
8   involved in   1.0
1   antifa also   1.0


Words : 
                 Bigrama  rank
18            user user   2.0
0   announcements every   1.0
1                any of   1.0
17             user url   1.0
16              url any   1.0
15               to 

            Bigrama  rank
0         are very   1.0
1   persuasive fam   1.0
2         user you   1.0
3  very persuasive   1.0
4          you are   1.0


Words : 
         Bigrama  rank
12      vote no   2.0
0     anyway we   1.0
1      going to   1.0
2   in november   1.0
3   liberals in   1.0
4       new she   1.0
5     no anyway   1.0
6         no to   1.0
7   nothing new   1.0
8       she was   1.0


Words : 
      Bigrama  rank
0  cool dude   1.0
1  user burt   1.0


Words : 
                Bigrama  rank
0               all in   1.0
1              are all   1.0
2          follow back   1.0
3            follow me   1.0
4     for hashtagtrump   1.0
5  hashtagtrump follow   1.0
6               if you   1.0
7               in for   1.0
8               me and   1.0
9          will follow   1.0


Words : 
        Bigrama  rank
0       at the   1.0
1   finally at   1.0
2      heat on   1.0
3     it again   1.0
4    okay with   1.0
5        on it   1.0
6  point where   1.0
7     so happy 

            Bigrama  rank
2           do not   2.0
12         they do   2.0
0     because they   1.0
9         not want   1.0
15        want you   1.0
14       user they   1.0
13      twitter is   1.0
11   sickening how   1.0
10  people because   1.0
8         not like   1.0


Words : 
       Bigrama  rank
0  doing life   1.0
1       he is   1.0
2    is doing   1.0
3    life tho   1.0
4     user he   1.0


Words : 
                  Bigrama  rank
30              the word   2.0
0                all the   1.0
23              so false   1.0
25           spread even   1.0
26          support them   1.0
27              that all   1.0
28  the hashtagdemocrats   1.0
29          the midterms   1.0
31          they support   1.0
32             those who   1.0


Words : 
                  Bigrama  rank
0              antifa is   1.0
11        or threatening   1.0
19             user user   1.0
18           user antifa   1.0
17          to professor   1.0
16            threats to   1.0
15  threat

                   Bigrama  rank
0             activist is   1.0
1             confirm the   1.0
16  user hashtagweakrinos   1.0
15           until proven   1.0
14                the man   1.0
13               the left   1.0
12          story changes   1.0
11          proven guilty   1.0
10                no hard   1.0
9                liar who   1.0


Words : 
         Bigrama  rank
0   also signed   1.0
1   as governor   1.0
2       bill as   1.0
3  control bill   1.0
4     first gun   1.0
5   governor of   1.0
6   gun control   1.0
7         of ca   1.0
8   reagan also   1.0
9    signed the   1.0


Words : 
          Bigrama  rank
0    awe hogwash   1.0
1          do we   1.0
2     hogwash do   1.0
3       need you   1.0
4  overstate the   1.0
5    really need   1.0
6    the obvious   1.0
7   to overstate   1.0
8       user awe   1.0
9      we really   1.0


Words : 
                  Bigrama  rank
0        backgrounds not   1.0
1                boom do   1.0
2     conservatives onl

...

        Bigrama  rank
0      as when   1.0
15      she is   1.0
27  witty like   1.0
26    when she   1.0
25   user user   1.0
24      to the   1.0
23      to see   1.0
22   think his   1.0
21    the sith   1.0
20     such as   1.0


Words : 
               Bigrama  rank
0           again the   1.0
14       my favourite   1.0
25          user user   1.0
24            user my   1.0
23             us boo   1.0
22              to us   1.0
21            this is   1.0
20        their minds   1.0
19      the democrats   1.0
18  the conservatives   1.0


Words : 
              Bigrama  rank
0        english for   1.0
1  for conservatives   1.0
2   learning english   1.0
3      user learning   1.0
4          user user   1.0


Words : 
         Bigrama  rank
0      ask your   1.0
1       at user   1.0
2  friends over   1.0
3       over at   1.0
4      user ask   1.0
5  your friends   1.0


Words : 
               Bigrama  rank
0     against muslims   1.0
1       crime against   1.0
20          

      Bigrama  rank
0     an nba   1.0
1      he is   1.0
2      is an   1.0
3  nba plant   1.0
4    user he   1.0


Words : 
               Bigrama  rank
0            and none   1.0
1            are just   1.0
20             up for   1.0
19             to her   1.0
18         to destroy   1.0
17         the alumni   1.0
16  stories democrats   1.0
15        standing up   1.0
14             of the   1.0
13           none are   1.0


Words : 
            Bigrama  rank
0     and entering   1.0
28       she calls   1.0
21        media as   1.0
22    petty crimes   1.0
23        plans to   1.0
24  rachel rollins   1.0
25       refuse to   1.0
26     running for   1.0
27      running in   1.0
29          she is   1.0


Words : 
       Bigrama  rank
0  and antifa   1.0
1    that and   1.0
2    user yes   1.0
3    yes that   1.0


Words : 
         Bigrama  rank
0        all of   1.0
13  of european   1.0
23     want all   1.0
22     user the   1.0
21  unless they   1.0
20    they want   1.0


               Bigrama  rank
0              and it   1.0
1     another fucking   1.0
2           antifa is   1.0
3  fucking pittsburgh   1.0
4         is glorious   1.0
5           is naming   1.0
6               it is   1.0
7           names and   1.0
8        naming names   1.0
9       philly antifa   1.0


Words : 
       Bigrama  rank
0  about life   1.0
1  clue about   1.0
2  hogg doesn   1.0
3   user hogg   1.0


Words : 
            Bigrama  rank
0          all the   1.0
1     as sensitive   1.0
2       labeled as   1.0
3       on twitter   1.0
4      people post   1.0
5          porn on   1.0
6        post porn   1.0
7  sensitive media   1.0
8         so funny   1.0
9         the time   1.0


Words : 
      Bigrama  rank
0    ain uor   1.0
1  uor kkkkk   1.0
2   user ain   1.0


Words : 
              Bigrama  rank
16         user user   4.0
9          in canada   1.0
15         user live   1.0
14        the advice   1.0
13        thanks for   1.0
12  rate coincidence   1.0
11 

          Bigrama  rank
0     2nd bottle   1.0
26       say the   1.0
20    or abolish   1.0
21     or anyone   1.0
22        or blm   1.0
23  or feminazis   1.0
24        or msm   1.0
25      reps are   1.0
27    see antifa   1.0
18      of vodka   1.0


Words : 
           Bigrama  rank
0           at up   1.0
1     is laughing   1.0
2  laughing while   1.0
3        looks at   1.0
4          she is   1.0
5       she looks   1.0
6        user she   1.0
7       while she   1.0


Words : 
               Bigrama  rank
10          user user   4.0
0   cameron bedfellow   1.0
1        clegg worked   1.0
2             for the   1.0
3              he was   1.0
4       ideal cameron   1.0
5           in europe   1.0
6           the ideal   1.0
7          the tories   1.0
8           tories in   1.0


Words : 
            Bigrama  rank
0       are making   1.0
1           as per   1.0
26         will be   1.0
25         user so   1.0
24      the saving   1.0
23       the leads   1.0
22         

ValueError: empty vocabulary; perhaps the documents only contain stop words